### Download entries from DIP-Bundestag and put them in a csv to further process them.

See https://search.dip.bundestag.de/api/v1/swagger-ui/ for the API reference. We only request documents of the type antwort and based on the start and end date provided.

In [ ]:
import requests
from pprint import pprint
import pandas as pd
from pathlib import Path
from pprint import pprint
from tqdm import tqdm
from concurrent.futures import ThreadPoolExecutor

DIP_URL = "https://search.dip.bundestag.de/api/v1/drucksache"
DIP_TOKEN = "rgsaY4U.oZRQKUHdJhF9qguHMkwCGIoLaqEcaHjYLF"

START_DATE = "2015-05-07"
END_DATE = "2023-07-09"

REQUEST_URL = f"{DIP_URL}?f.drucksachetyp=Antwort&f.datum.start={START_DATE}&f.datum.end={END_DATE}&format=json&apikey={DIP_TOKEN}"

df = pd.DataFrame()
docs = []
res = requests.get(REQUEST_URL)
r_json = res.json()
old_cursor = r_json["cursor"]

with ThreadPoolExecutor(max_workers=10) as pool:
    count = 0
    while True:
        for doc in tqdm(r_json["documents"]):
            docs.append(doc)
            doc_id = doc["id"]
            doc_number = doc["fundstelle"]["dokumentnummer"]
            url = doc["fundstelle"]["pdf_url"]            
            count += 1
        res = requests.get(f"{REQUEST_URL}&cursor={old_cursor}")
        r_json = res.json()
        new_cursor = r_json["cursor"]
        if new_cursor == old_cursor:
            print("Found same cursor. No new results.")
            break
        old_cursor = new_cursor


df = df.from_records(docs)
print(f"Extracted {len(df)} entries.")
df.to_csv("raw_entries.csv")

### Read back csv written in previous step, and download the associated PDF with each entry

In [ ]:

df = pd.read_csv("raw_entries.csv")

def download_file(download_path:Path,doc_id:str,url:str) -> None:
    r = requests.get(url, allow_redirects=True)
    if r.status_code != 200:
        print(f"Got status {r.status_code} for url {doc_id} and {url}")
        return False
    with open(download_path / f"{doc_id}.pdf", 'wb') as f:
        f.write(r.content)
    
    return True

download_path = Path("./downloads2/")
download_path.mkdir(exist_ok=True)


for i,row in df.iterrows():
    pdf_url = eval(row["fundstelle"])["pdf_url"]
    success = download_file(download_path,row["id"],pdf_url)
    df.at[i,"download_success"]=success

df.to_csv("entries_with_download_status.csv")


### Extract the text out of the downloaded pdfs

In [ ]:
import pandas as pd
import sys
import pdftotext
import fitz
import re
from pathlib import Path
from dehyphen import FlairScorer
from dehyphen import format
from tqdm import tqdm

HEADER_HEIGHT = 78
FOOTER_HEIGHT = 70

QUESTION_FONT_SIZE = 9.609999656677246
ANSWER_FONT_SIZE = 10.678000450134277
BULLET_POINT_ANSWER_SIZE = 6.0

OUTPUT_PATH = 'raw_text_blocks.csv'

scorer = FlairScorer(lang="de")
pattern = r'^\s*\d+\.\s*' # Matches a number followed by a dot and a space at the beginning of the string


def process_text_block(block:dict = {},pdf_path:Path = None,remove_q_numbers: bool = False):
    txt = []
    font = None

    for line in block.get("lines", []):
        for span in line["spans"]:
            span_txt = span["text"]
            span_font = span["font"]
            span_font_size = span["size"]
            if span_txt=="" or span_txt.isspace():
                #print(f"Found empty string or only spaces in document {pdf_path}")
                continue
            if font is None:
                span_type = "Unknown"
                if span_font_size == QUESTION_FONT_SIZE:
                    span_type = "Question"
                    if remove_q_numbers:
                        span_txt = re.sub(pattern,"",span_txt)
                elif span_font_size in [BULLET_POINT_ANSWER_SIZE,ANSWER_FONT_SIZE]:
                    span_type = "Answer"
                font = (span_font, span_font_size, span_type)
            txt.append(span_txt)

    if len(txt) > 1:
        txt_joined = "\n".join(txt)
        txt_formatted = format.text_to_format(txt_joined)
        txt_dehyphenated = scorer.dehyphen(txt_formatted)
        txt = format.format_to_text(txt_dehyphenated)
    else:
        if len(txt) == 0:
            txt = ""
        else:
            txt = txt[0]
    txt = txt.strip()
    if font is not None:
        result = {"file": pdf_path.name, "txt": txt, "font": font[0], "size": font[1], "type": font[2]}
    else:
        result = {"file": pdf_path.name, "txt": "Error", "font": "Error", "size":"Error", "type": "Error"}
    return result


processed = []
if Path(OUTPUT_PATH).exists():
    df = pd.read_csv(OUTPUT_PATH,sep="|")
    processed = df["file"].values
else:
    df = pd.DataFrame()

res = []
for pdf_path in tqdm(Path("./downloads2").glob("*.pdf"),desc="docs"):

    if pdf_path.name in processed:
        print(f"Found pdf in df: {pdf_path}")
        continue

    doc = fitz.open(pdf_path) # open a document

    for i,page in enumerate(doc):  # iterate the document pages
        #page.draw_rect([0,HEADER_HEIGHT,page.rect.width,page.rect.height - FOOTER_HEIGHT])
        res_raw = page.get_text("dict",clip = [0,HEADER_HEIGHT,page.rect.width,page.rect.height - FOOTER_HEIGHT])
        blocks = res_raw["blocks"] # blocks on page

        for block in blocks:
            try:
                block_res = process_text_block(block,pdf_path)
                if block_res["type"] != "Unknown" and  block_res["type"] != "Error":
                    res.append(block_res)
            except Exception as e:
                print(str(e),block)


    #print(len(res))
    if len(res) > 100:
        df = pd.DataFrame.from_dict(res)

        df.to_csv(OUTPUT_PATH, mode='a', header=not Path(OUTPUT_PATH).exists(),index=False,sep="|")
        df = pd.DataFrame()
        res = []


### Transform raw text into question / answer tuples

In [ ]:
df_f = pd.read_csv("./raw_text_blocks.csv",sep="|")
print(len(df_f))
files = df_f.groupby('file')

pairs = []
for i,group in files:

    i = iter(group.groupby([(group.type != group.type.shift()).cumsum()]))

    try:
        while True:
            elem1 = next(i)
            if set(elem1[1].type.values) != {"Question"}:
                print("Broken")
                continue
            elem2 = next(i)
            if set(elem2[1].type.values) != {"Answer"}:
                print("Broken")
                continue

            pair = {}
            pair["question"] = "\n".join(list(elem1[1].txt.values))
            pair["answer"] = "\n".join(list(elem2[1].txt.values))
            pair["doc_id"] = group.file.unique()[0].split(".")[0]
            pairs.append(pair)
    except StopIteration:
        pass
    
df_res = pd.DataFrame.from_records(pairs)
df_res.to_csv("final.csv")